import AETransformation
import AEWMVFTS
import PreProcessing
from sklearn.metrics import mean_absolute_error
import math
from pyFTS.common import Util
import datetime
import statistics
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from keras.models import Model
from keras.layers import Dense, Input
from keras import regularizers
from sklearn.preprocessing import MinMaxScaler
import pyFTS
from pyFTS.benchmarks import Measures
import statistics
from pyFTS.common.Util import persist_obj, load_obj
from pyFTS.models.multivariate import common, variable, wmvfts
from pyFTS.partitioners import Grid
from pyFTS.common import Membership

In [2]:
df = pd.read_csv('household_power_consumption.csv')
#data = df.drop(labels=['icon','summary','cloudCover', 'House overall [kW]', 'time'], axis=1)
#data = data.loc[0: : 10]
#data.reset_index(inplace=True)
#data.pop('index')

In [4]:
def clean_dataset(df):
    assert isinstance(df, pd.DataFrame) 
    df.dropna(inplace=True)
    indices_to_keep = ~df.isin([np.nan, np.inf, -np.inf]).any(1)
    return df[indices_to_keep].astype(np.float64)

In [13]:
data = pd.read_csv('household_power_consumption.csv', sep = ";")
data = data.drop(labels=['Time','Date'], axis=1)
#data = data.loc[0: : 30] # 30 minutes
data.dropna(inplace = True)
data = clean_dataset(data)
data.head()

/usr/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3441: DtypeWarning: Columns (2,3,4,5,6,7) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


Global_active_power  Global_reactive_power  Voltage  Global_intensity  \
0                4.216                  0.418   234.84              18.4   
1                5.360                  0.436   233.63              23.0   
2                5.374                  0.498   233.29              23.0   
3                5.388                  0.502   233.74              23.0   
4                3.666                  0.528   235.68              15.8   

   Sub_metering_1  Sub_metering_2  Sub_metering_3  
0             0.0             1.0            17.0  
1             0.0             1.0            16.0  
2             0.0             2.0            17.0  
3             0.0             1.0            17.0  
4             0.0             1.0            17.0

In [19]:
names = ['factor_1']

In [7]:
def sliding_window_AE(data,n_windows,train_size,dim,fs, names):
    ae_wmvfts = AEWMVFTS.AEWeightedMVFTS(n_dimensions = dim,n_part = fs,endogen_variable='Global_active_power',names=names)
    
    result = {
         "window": [],
         "rmse": [],
         "mape": [],
         "smape": [],
         "mae": []
    }

    order = 1
    tam = len(data)
    n_windows = 30
    windows_length = math.floor(tam / n_windows)
    for ct, ttrain, ttest in Util.sliding_window(data, windows_length, 0.75, inc=1):
        if len(ttest) > 0:
        
            data_train = ttrain.loc[:,'Global_active_power':'Sub_metering_3']
            data_test = ttest.loc[:,'Global_active_power':'Sub_metering_3']
        
        
            print('-' * 20)
            print(f'training window {(ct)}')
            model, ae_reduced_train = ae_wmvfts.run_train_model(data=data_train, epochs=50, n_layers=2, neuron_per_layer=[50,dim], batch=40, opt='adagrad', act='softsign')
            forecast, forecast_self, ae_reduced_test = ae_wmvfts.run_test_model(model=model, data=data_test, epochs=50, n_layers=2,
                                                           neuron_per_layer=[50,dim], batch=40, opt='adagrad', act='aoftsign')
        
        #Teste e cálculo dos erros da previsão
        #appliance_test = ttest['Appliances_t+1'].values
        
        #Teste e cálculo dos erros da previsão - valor use  é Appliances o use Appliances_t+1 --> label igual por causa do model
            print("[{0: %H:%M:%S}]".format(datetime.datetime.now()) + f" getting statistics")
            rmse = Measures.rmse(ae_reduced_test['Global_active_power'].values.tolist(),forecast)
            mape = Measures.mape(ae_reduced_test['Global_active_power'].values.tolist(),forecast)
            smape = Measures.smape(ae_reduced_test['Global_active_power'].values.tolist(),forecast)
        
            forecast = pd.DataFrame(forecast)
            forecast.fillna(forecast.mean(),inplace=True)
            forecast = np.array(forecast).reshape(-1)
            mae = mean_absolute_error(ae_reduced_test['Global_active_power'].values.tolist(), forecast)
        
        # Grafico de comparação Original x Previsto para cada janela
        #fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[15, 3])
        #ax.plot(pca_reduced_test['Appliances'], label='Original')
        #ax.plot(forecast, label='Forecast')
        #handles, labels = ax.get_legend_handles_labels()
        #lgd = ax.legend(handles, labels, loc=2, bbox_to_anchor=(1, 1))
        #plt.show()
        
            result["rmse"].append(rmse)
            result["mape"].append(mape)
            result["smape"].append(smape)
            result["mae"].append(mae)
            result["window"].append(ct)
        
            
    measures = pd.DataFrame(result)
    return measures

In [21]:
dimensions = [2]
fuzzy_sets = [50]

final_result = {
    "dimensions": [],
    "fuzzy_sets": [],
    "rmse": [],
    "mae": [],
    "mape": [],
    "smape": []
}

n_windows = 30
train_size = 0.75

for dim in dimensions:
    names.append('factor_'+str(dim))
    print (names)
    for fs in fuzzy_sets:
        measures = sliding_window_AE(data,n_windows,train_size,dim,fs, names)
        final_result["dimensions"].append(dim)
        final_result["fuzzy_sets"].append(fs)
        
        rmse = round(statistics.mean(measures['rmse']),3)
        mape = round(statistics.mean(measures['mape']),3)
        smape = round(statistics.mean(measures['smape']),3)
        mae = round(statistics.mean(measures['mae']),3)
        
        final_result["rmse"].append(rmse)
        final_result["mape"].append(mape)
        final_result["smape"].append(smape)
        final_result["mae"].append(mae)
        
        print(f'Results: {(dim,fs,rmse,mae,mape,smape)}')
        
        
final_measures_ae = pd.DataFrame(final_result) 

print("Statistics AE-WMVFTS (test): ")
final_measures_ae

['factor_1', 'factor_2']
--------------------
training window 0
Epoch 1/50


/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


1708/1708 [==============================] - 2s 1ms/step - loss: 0.0169
Epoch 2/50
1708/1708 [==============================] - 2s 1ms/step - loss: 0.0075
Epoch 3/50
1708/1708 [==============================] - 2s 1ms/step - loss: 0.0069
Epoch 4/50
1708/1708 [==============================] - 2s 1ms/step - loss: 0.0067
Epoch 5/50
1708/1708 [==============================] - 2s 1ms/step - loss: 0.0066
Epoch 6/50
1708/1708 [==============================] - 2s 1ms/step - loss: 0.0066
Epoch 7/50
1708/1708 [==============================] - 2s 1ms/step - loss: 0.0066
Epoch 8/50
1708/1708 [==============================] - 2s 1ms/step - loss: 0.0066
Epoch 9/50
1708/1708 [==============================] - 2s 1ms/step - loss: 0.0066
Epoch 10/50
1708/1708 [==============================] - 2s 1ms/step - loss: 0.0065
Epoch 11/50
1708/1708 [==============================] - 3s 2ms/step - loss: 0.0065
Epoch 12/50
1708/1708 [==============================] - 3s 1ms/step - loss: 0.0065
Epoch 13/50


/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


Epoch 1/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0373
Epoch 2/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0109
Epoch 3/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0093
Epoch 4/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0087
Epoch 5/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0082
Epoch 6/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0077
Epoch 7/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0072
Epoch 8/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0069
Epoch 9/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0066
Epoch 10/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0065
Epoch 11/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0064
Epoch 12/50
570/570 [==============================] - 1s 1ms/step - loss: 0.0064
Epoch 13/50
570/570 [====

...

/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


Epoch 1/50
570/570 [==============================] - 3s 3ms/step - loss: 0.0375
Epoch 2/50
570/570 [==============================] - 2s 4ms/step - loss: 0.0086
Epoch 3/50
570/570 [==============================] - 2s 4ms/step - loss: 0.0066
Epoch 4/50
570/570 [==============================] - 3s 5ms/step - loss: 0.0060
Epoch 5/50
570/570 [==============================] - 2s 4ms/step - loss: 0.0057
Epoch 6/50
570/570 [==============================] - 2s 4ms/step - loss: 0.0055
Epoch 7/50
570/570 [==============================] - 2s 4ms/step - loss: 0.0054
Epoch 8/50
570/570 [==============================] - 3s 5ms/step - loss: 0.0054
Epoch 9/50
570/570 [==============================] - 2s 4ms/step - loss: 0.0053
Epoch 10/50
570/570 [==============================] - 2s 4ms/step - loss: 0.0053
Epoch 11/50
570/570 [==============================] - 2s 4ms/step - loss: 0.0053
Epoch 12/50
570/570 [==============================] - 2s 4ms/step - loss: 0.0052
Epoch 13/50
570/570 [====

/home/luizf/.local/lib/python3.9/site-packages/pyFTS/models/multivariate/mvfts.py:165: RuntimeWarning: invalid value encountered in double_scalars
  ret.append(np.dot(mv,mp.T)/np.nansum(mv))


[ 12:54:32] getting statistics
Results: (2, 50, 0.023, 0.007, 0.341, 0.168)
Statistics AE-WMVFTS (test): 


dimensions  fuzzy_sets   rmse    mae   mape  smape
0           2          50  0.023  0.007  0.341  0.168

In [9]:
data = pd.read_csv('household_power_consumption.csv', sep = ";")
data = data.drop(labels=['Time','Date'], axis=1)
data = data.loc[0: : 30] # 30 minutes
data.dropna(inplace = True)
data = clean_dataset(data)
data.head()

/usr/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3441: DtypeWarning: Columns (2,3,4,5,6,7) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


Global_active_power  Global_reactive_power  Voltage  Global_intensity  \
0                  4.216                  0.418   234.84              18.4   
30                 2.720                  0.000   235.06              11.6   
60                 3.452                  0.000   235.20              15.2   
90                 4.298                  0.000   232.39              18.4   
120                3.262                  0.052   232.64              14.0   

     Sub_metering_1  Sub_metering_2  Sub_metering_3  
0               0.0             1.0            17.0  
30              0.0             0.0            17.0  
60              0.0             1.0            17.0  
90              0.0             1.0            16.0  
120             0.0             0.0            17.0

In [10]:
dimensions = [2,3,4]
fuzzy_sets = [10,20,30,40,50]
names = ['factor_1']

final_result = {
    "dimensions": [],
    "fuzzy_sets": [],
    "rmse": [],
    "mae": [],
    "mape": [],
    "smape": []
}

n_windows = 30
train_size = 0.75

for dim in dimensions:
    names.append('factor_'+str(dim))
    print (names)
    for fs in fuzzy_sets:
        measures = sliding_window_AE(data,n_windows,train_size,dim,fs, names)
        final_result["dimensions"].append(dim)
        final_result["fuzzy_sets"].append(fs)
        
        rmse = round(statistics.mean(measures['rmse']),3)
        mape = round(statistics.mean(measures['mape']),3)
        smape = round(statistics.mean(measures['smape']),3)
        mae = round(statistics.mean(measures['mae']),3)
        
        final_result["rmse"].append(rmse)
        final_result["mape"].append(mape)
        final_result["smape"].append(smape)
        final_result["mae"].append(mae)
        
        print(f'Results: {(dim,fs,rmse,mae,mape,smape)}')
        
        
final_measures_ae = pd.DataFrame(final_result) 

print("Statistics AE-WMVFTS (test): ")
final_measures_ae

['factor_1', 'factor_2']
--------------------
training window 0
Epoch 1/50


/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


57/57 [==============================] - 1s 1ms/step - loss: 0.1086
Epoch 2/50
57/57 [==============================] - 0s 1ms/step - loss: 0.0726
Epoch 3/50
57/57 [==============================] - 0s 1ms/step - loss: 0.0517
Epoch 4/50
57/57 [==============================] - 0s 1ms/step - loss: 0.0397
Epoch 5/50
57/57 [==============================] - 0s 1ms/step - loss: 0.0324
Epoch 6/50
57/57 [==============================] - 0s 1ms/step - loss: 0.0274
Epoch 7/50
57/57 [==============================] - 0s 1ms/step - loss: 0.0234
Epoch 8/50
57/57 [==============================] - 0s 1ms/step - loss: 0.0202
Epoch 9/50
57/57 [==============================] - 0s 1ms/step - loss: 0.0176
Epoch 10/50
57/57 [==============================] - 0s 2ms/step - loss: 0.0157
Epoch 11/50
57/57 [==============================] - 0s 2ms/step - loss: 0.0144
Epoch 12/50
57/57 [==============================] - 0s 3ms/step - loss: 0.0134
Epoch 13/50
57/57 [==============================] - 0s 3ms/

/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


Epoch 1/50
19/19 [==============================] - 0s 999us/step - loss: 0.1988
Epoch 2/50
19/19 [==============================] - 0s 1ms/step - loss: 0.1529
Epoch 3/50
19/19 [==============================] - 0s 1ms/step - loss: 0.1273
Epoch 4/50
19/19 [==============================] - 0s 1ms/step - loss: 0.1101
Epoch 5/50
19/19 [==============================] - 0s 1ms/step - loss: 0.0968
Epoch 6/50
19/19 [==============================] - 0s 1ms/step - loss: 0.0853
Epoch 7/50
19/19 [==============================] - 0s 2ms/step - loss: 0.0759
Epoch 8/50
19/19 [==============================] - 0s 2ms/step - loss: 0.0683
Epoch 9/50
19/19 [==============================] - 0s 2ms/step - loss: 0.0622
Epoch 10/50
19/19 [==============================] - 0s 1ms/step - loss: 0.0577
Epoch 11/50
19/19 [==============================] - 0s 1ms/step - loss: 0.0541
Epoch 12/50
19/19 [==============================] - 0s 2ms/step - loss: 0.0513
Epoch 13/50
19/19 [============================

...

/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


Epoch 1/50
19/19 [==============================] - 0s 598us/step - loss: 0.1166
Epoch 2/50
19/19 [==============================] - 0s 615us/step - loss: 0.0917
Epoch 3/50
19/19 [==============================] - 0s 607us/step - loss: 0.0789
Epoch 4/50
19/19 [==============================] - 0s 637us/step - loss: 0.0682
Epoch 5/50
19/19 [==============================] - 0s 660us/step - loss: 0.0588
Epoch 6/50
19/19 [==============================] - 0s 681us/step - loss: 0.0505
Epoch 7/50
19/19 [==============================] - 0s 733us/step - loss: 0.0440
Epoch 8/50
19/19 [==============================] - 0s 782us/step - loss: 0.0392
Epoch 9/50
19/19 [==============================] - 0s 730us/step - loss: 0.0358
Epoch 10/50
19/19 [==============================] - 0s 751us/step - loss: 0.0333
Epoch 11/50
19/19 [==============================] - 0s 722us/step - loss: 0.0309
Epoch 12/50
19/19 [==============================] - 0s 833us/step - loss: 0.0284
Epoch 13/50
19/19 [======

/home/luizf/.local/lib/python3.9/site-packages/pyFTS/models/multivariate/mvfts.py:165: RuntimeWarning: invalid value encountered in double_scalars
  ret.append(np.dot(mv,mp.T)/np.nansum(mv))


[ 14:02:00] getting statistics
Results: (4, 50, 0.0, 0.003, 0.002, 0.001)
Statistics AE-WMVFTS (test): 


dimensions  fuzzy_sets   rmse    mae    mape  smape
0            2          10  0.202  0.138  22.536  7.938
1            2          20  0.099  0.051   6.173  2.114
2            2          30  0.063  0.023   2.890  1.015
3            2          40  0.045  0.026   4.383  1.427
4            2          50  0.046  0.010   2.191  0.565
5            3          10  0.112  0.064   8.597  3.047
6            3          20  0.034  0.013   4.588  1.196
7            3          30  0.016  0.005   0.308  0.119
8            3          40  0.013  0.005   0.686  0.220
9            3          50  0.003  0.003   0.141  0.061
10           4          10  0.072  0.029   5.271  1.877
11           4          20  0.007  0.004   0.063  0.028
12           4          30  0.003  0.003   0.053  0.025
13           4          40  0.001  0.003   0.004  0.002
14           4          50  0.000  0.003   0.002  0.001

In [11]:
final_measures_ae.to_csv (r'ae_wmvfts_dim_fsets_hpc_uci.csv', index = False, header=True)